#Exercise for PySpark
ใช้ Table ที่กำหนดให้ด้านล่างในการเขียน PySpark  
- c360_l0.profile_drm_t_active_profile_customer_journey  
- c360_l0.billing_rt_t_recharge_daily

(Q1) Query ข้อมูลจากถัง c360_l0.profile_drm_t_active_profile_customer_journey และเก็บลงในตัวแปร profile_df โดยมีเงื่อนไขดังนี้  
- ใช้ข้อมูล ณ เดือน กุมภา2022
- ดูแค่ลูกค้า Pre-paid
- ใช้แค่ register_date ,access_method_num ,network_type ,norms_net_revenue ,norms_voice_minute ,norms_mb_gprs_volume
- เปลี่ยนชื่อ Column  
norms_net_revenue --> arpu_thb  
norms_voice_minute --> mou_minute  
norms_mb_gprs_volume --> vou_mb
- กำหนดกลุ่มโดยใช้ rule based ดังนี้  
vou น้อยกว่า 1 GB , mou น้อยกว่า 10 นาที -- > low_usage  
vou มากกว่า 1 GB , mou น้อยกว่า 10 นาที -- > data_user  
vou มากกว่า 1 GB , mou มากกว่า 10 นาที -- > heavy_user
vou น้อยกว่า 1 GB , mou มากกว่า 10 นาที -- > voice_user

In [0]:
%sql
show partitions c360_l0.profile_drm_t_active_profile_customer_journey 

partition partition_month=201908 partition_month=201909 partition_month=201910 partition_month=201911 partition_month=201912 partition_month=202001 partition_month=202002 partition_month=202003 partition_month=202004 partition_month=202005 partition_month=202006 partition_month=202007 partition_month=202008 partition_month=202009 partition_month=202010 partition_month=202011 partition_month=202012 partition_month=202101 partition_month=202102 partition_month=202103 partition_month=202104 partition_month=202105 partition_month=202106 partition_month=202107 partition_month=202108 partition_month=202109 partition_month=202110 partition_month=202111 partition_month=202112 partition_month=202201 partition_month=202202

In [0]:
import pyspark.sql.functions as F
from pyspark.sql.functions  import col,when

In [0]:
df = spark.table('c360_l0.profile_drm_t_active_profile_customer_journey')
df.display()

month_id access_method_num register_date customer_id ba_id sff_subscription_id crm_sub_id sim_serial_no charge_type billing_system mobile_status network_type mobile_segment customer_type crm_most_usage_region crm_most_usage_province crm_most_usage_amphur crm_most_usage_tumbol first_act_province_th first_act_region imei handset_brand_code handset_brand_name handset_model_code handset_model_name handset_dual_sim ais_handset_technology max_system_technology handset_support_3g_2100_yn handset_type handset_os handset_standby_mode handset_launchprice handset_saleprice key_sub handset_status_flag handset_movement service_month service_month_range main_promo_id main_promo_name birth_date age gender bill_media p1_mobile_segment p1_handset_brand_code p1_handset_brand_name p1_handset_model_code p1_handset_model_name p1_handset_dual_sim p1_ais_handset_technology p1_handset_support_3g_2100_yn p1_handset_type p1_handset_os p1_handset_standby_mode p1_handset_launchprice p1_handset_saleprice card_no same_card_id_post same_card_id_pre data_user_yn p1_data_user_yn zero_arpu_yn p1_zero_arpu_yn trade_project_type trade_project_type_desc trade_number trade_name return_cd ussd_cd trade_serial_num trade_sale_month trade_product_brand trade_product_model trade_price_range trade_cmd_channel_type trade_location_region contract_lock_duration remain_contract_duration contract_start_month contract_end_month contract_end_yn contract_type trade_card_id trade_contract_hs_range trade_join_package trade_order_type last_usage_match_yn current_hs_active_yn current_sim_active_yn curr_summary_last_usage curr_mobile_imei_technology trade_handset_os trade_handset_standby_mode trade_handset_launchprice trade_handset_saleprice flag_join_campaign_hs_bundle flag_join_campaign_hs_only amendment_reason_code amendment_reason_name pa_group segment_expire_month p1_segment_expire_month status_next1_mth status_next2_mth status_next3_mth order_type_new norms_net_revenue norms_voice_minute norms_net_revenue_avg_3mth norms_net_revenue_avg_3mth_range norms_net_revenue_avg_6mth_range norms_net_revenue_avg_3mth_p0_p2 norms_mb_gprs_volume norms_net_revenue_gprs norms_net_revenue_vas norms_net_revenue_voice p1_norms_net_revenue p1_norms_voice_minute p1_norms_mb_gprs_volume p1_norms_net_revenue_gprs p1_norms_net_revenue_vas p1_norms_net_revenue_voice p1_norms_net_revenue_avg_3mth p1_norms_net_revenue_avg_3mth_ran p2_norms_net_revenue p2_norms_voice_minute p2_norms_mb_gprs_volume p2_norms_net_revenue_gprs p2_norms_net_revenue_vas p2_norms_net_revenue_voice total_recharge prv_imei prv_imei_eff_dttm prv_imei_end_dttm prv_change_device_brand_code prv_change_device_brand_name prv_change_device_model_code prv_change_device_model_name prv_change_device_type prv_change_device_os prv_change_device_standby_mode prv_change_device_dual_sim prv_change_device_launchprice prv_change_device_saleprice prv_change_device_ais_technology handset_aging max_system_usage p1_max_system_usage prv_imei_first_eff_dttm order_date_new order_channel_new moc_cust_type regional_region regional_province imei_eff_dttm imei_end_dttm imei_first_eff_dttm prv_handset_aging trade_location_code trade_location_name trade_location_province_th c360_subscription_identifier product_type no_of_mob_post_same_id_card no_of_mob_pre_same_id_card no_of_fbb_same_id_card no_of_mob_same_id_card no_of_mob_fbb_same_id_card no_of_sim_online_same_id_card verify_card_no_yn no_of_mob_pre_same_id_card_exc_ct no_of_mob_same_id_card_exc_ct no_of_mob_fbb_same_id_card_exc_ct no_of_sim_online_same_id_card_exc_ct pretty_lucky_number province_new_base_line province_new_base_line_code region_new_base_line crm_most_usage_amphur_th crm_most_usage_province_th renew_flag last_renew_date partition_month 2019-08-31T00:00:00.000+0000 70cQoGzw19joZlh5R4y2Ly8lcbk9kdHO0LPY7QqlWyrQKNE7S+N9YVrlivICNSh0 2019-08-08T00:00:00.000+0000 613367862J74Asx null null 1-10ENCR2K 1920611314556 Pre-paid INS SA 3GPre-paid Classic I NU CHIANG MAI Doi Lo ยางคราม เชียงใหม่ NU 8672110

In [0]:
# vou น้อยกว่า 1 GB , mou น้อยกว่า 10 นาที -- > low_usage
# vou มากกว่า 1 GB , mou น้อยกว่า 10 นาที -- > data_user
# vou มากกว่า 1 GB , mou มากกว่า 10 นาที -- > heavy_user 
# vou น้อยกว่า 1 GB , mou มากกว่า 10 นาที -- > voice_user


# norms_net_revenue --> arpu_thb
# norms_voice_minute --> mou_minute
# norms_mb_gprs_volume --> vou_mb

profile_df = spark.table('c360_l0.profile_drm_t_active_profile_customer_journey').select('register_date' ,'access_method_num' ,'network_type','norms_net_revenue' ,'norms_voice_minute' ,'norms_mb_gprs_volume')\
.filter((col('partition_month') == '202202') & (col("network_type") == '3GPre-paid'))\
.withColumnRenamed('norms_net_revenue','arpu_thb')\
.withColumnRenamed('norms_voice_minute','mou_minute')\
.withColumnRenamed('norms_mb_gprs_volume','vou_mb')\
.withColumn('voice_user',when((col("vou_mb") < 1/1024) & (col("mou_minute") < 10),'low_usage')\
                        .when((col("vou_mb") > 1/1024) & (col("mou_minute") < 10),'data_user')\
                        .when((col("vou_mb") > 1/1024) & (col("mou_minute") > 10),'heavy_user')\
                        .when((col("vou_mb") < 1/1024) & (col("mou_minute") > 10),'voice_user')\
                        .otherwise('other'))


(Q2) Query ข้อมูลจากถัง c360_l0.billing_rt_t_recharge_daily และเก็บลงในตัวแปร top_up_df โดยมีเงื่อนไขดังนี้  
- ใช้ข้อมูล ณ เดือน กุมภา2022
- ต้องการ column ดังนี้  
sum_face_value จำนวนเงินที่ Top up ทั้งหมด  
avg_face_value จำนวนเงินที่ Top up เฉลี่ยต่อครั้ง  
no_recharge_date จำนวนวันที่เติมเงินทั้งหมด

ปล. face_value คือจำนวนเงินที่เติมเงินต่อครั้ง ,recharge_date คือวันที่ลูกค้าเติมเงิน

In [0]:
spark.table('c360_l0.billing_rt_t_recharge_daily').display()

recharge_date access_method_num month_id tariff_plan_id activate_location recharge_type face_value first_province mobile_region register_date dealer_code dealer_region quantity dealer_province flag_dealer_area account_id coverage_type recharge_time flag_dealer_in_out_region invoicing_company billing_system dealer_name recharge_type_name recharge_type_group recharge_type_sub_group region_code province_name credit_card_no credit_card_type partition_date 2019-08-01T00:00:00.000+0000 E8QZK3hOtymo.D4Q+sSCA8YhtnrhxCBnM8EYb04sfub7n6DC79DgHWvvQaSM4YS5 2019-08-31T00:00:00.000+0000 P17058302 T00811679003123 B78 50.0 SPN null null 10743 null null null I 613048932213320 One Province 2019-08-01T19:05:17.000+0000 I AIS INS BOONTERM mPay_Boonterm mPay Vending mPay Vending CB Samut Prakan null null 20190801 2019-08-01T00:00:00.000+0000 42PgTJHw4TSdAWBID9MDKEm9+0.mew5kgS7CHEPC16AmBcXnDoC52wlVZhzgFdLm 2019-08-31T00:00:00.000+0000 624 T07720401858101 32 20.0 NMA XL 2010-12-29T00:00:00.000+0000 10603 null null null I 3148108239 One Province 2019-08-01T07:18:03.000+0000 I AWN null AIS KIOSK mPay (Agent mCash) mPay Vending mPay Vending XL Nakhon Ratchasima null null 20190801 2019-08-01T00:00:00.000+0000 OtL9cECLF7Cdj97LeZsJ7EArYz1mZj6znFl9bdA3GiQQk0GzL8E8IrAWI4q5Og7T 2019-08-31T00:00:00.000+0000 1346 L0622550032 B78 20.0 CTI null 2018-08-15T00:00:00.000+0000 10743 null null null I 105830002928215249 One Province 2019-08-01T07:55:08.000+0000 I AIS CBS BOONTERM mPay_Boonterm mPay Vending mPay Vending CE Chanthaburi null null 20190801 2019-08-01T00:00:00.000+0000 K0Pe0tEcf87HB.l5RCUm6wHdF4o0BP.ImUNkn+BUlNpAZWaFxyGsMLHv31H+b2O. 2019-08-31T00:00:00.000+0000 182 T25378463959107 B43 20.0 NBP XU 2012-05-06T00:00:00.000+0000 11434 null null null I 193570002883163762 One Province 2019-08-01T09:12:36.000+0000 I AIS CBS Vending Corporation Recharge via mPay (Agent mCash) mPay Vending mPay Vending XU Nong Bua Lam Poo null null 20190801 2019-08-01T00:00:00.000+0000 UcgEOh4w3.PCqzLDR0GwLiGxV7.c5iVTrbo1+SkO6kwSR+tEzNa4cVji6TG7UeEe 2019-08-31T00:00:00.000+0000 126 T19736220328112 32 100.0 PKN CW 2006-04-08T00:00:00.000+0000 10883 null null null I 5158206822 One Province 2019-08-01T09:58:34.000+0000 I AWN null Twin Lotus mPay (Agent mCash) mPay Non-Vending mPay Non-Vending CW Prachuap Khiri Khan null null 20190801 2019-08-01T00:00:00.000+0000 FhbgIN3UoTPzcFh9A9ZZVDx90qJk2PUcoHRU2x2uGbUI7GEvnWZMywFh.l7yBpvW 2019-08-31T00:00:00.000+0000 P17058302 L0525513961 B0 50.0 PRI null 2017-10-21T00:00:00.000+0000 1100001010 CB 3000.0 BKK O 632641613H6DDqo One Province 2019-08-01T17:40:47.000+0000 O AIS INS สห ลอว์สัน Cash card Cash card Cash card CE Prachin Buri null null 20190801 2019-08-01T00:00:00.000+0000 .ehd.TTC0qJa8nInfSBDU3wfcZGiDlwgeFBnzMpRn5tXdZxPgat9wPeXHeHuU0lg 2019-08-31T00:00:00.000+0000 1381 L0182511723 51 30.0 PNA SU 2013-03-06T00:00:00.000+0000 00100461830000065752 SU null PNA I 4145250938 One Province 2019-08-01T15:33:47.000+0000 I AWN null null Refill on Mobile ROM ROM SU Phang nga null null 20190801 2019-08-01T00:00:00.000+0000 g8HPaD7TL5jf4ebVQWSz9BB7AI9eyF2Nm8QI2RCBL0WbHcR.4OdeS9nk5LDuVQGd 2019-08-31T00:00:00.000+0000 1277 L0646520004 B50 100.0 KSN XL 2018-10-01T00:00:00.000+0000 00100312480000066228 XU null KSN I 157130002801542789 One Province 2019-08-01T15:11:54.000+0000 I AWN CBS null Refill on Mobile ROM ROM XU Kalasin null null 20190801 2019-08-01T00:00:00.000+0000 ls4YfG4zghR0kCkQcoh1AKiCw9ZomiDNt4D9AjkUhIIKl5oOYOqw1Y9kLqmLUHcK 2019-08-31T00:00:00.000+0000 1087 null 51 30.0 null null 2015-07-14T00:00:00.000+0000 11000001170000000439 CB null BKK I 4155109262 One Province 2019-08-01T19:27:27.000+0000 I AWN null null Refill on Mobile ROM ROM null null null null 20190801 2019-08-01T00:00:00.000+0000 ICVa7y9.ehV7QTDQA1+2B.sh.y2k40fGCCQ+zAh96YkeJ0qMVT5OEgYxJ2AgNTs8 2019-08-31T00:00:00.000+0000 1369 T10016463507112 B78 30.0 BKN null 2019-01-10T00:00:00.000+0000 10743 null null null I 256880002986327538 One Province 2019-08-01T01:38:36.000+0000 I AIS CBS BO

In [0]:
top_up_df  = spark.table('c360_l0.billing_rt_t_recharge_daily').filter(col("partition_date").between ('20220201','20220228')).groupBy('access_method_num','register_date')\
.agg(F.sum("face_value").alias('sum_face_value')\
     ,F.avg("face_value").alias('avg_face_value')\
    ,F.countDistinct("recharge_date").alias('no_recharge_date'))

# .select('register_date' ,'access_method_num' ,'network_type','norms_net_revenue' ,'norms_voice_minute' ,'norms_mb_gprs_volume')

(Q3) นำ profile_df และ top_up_df ที่ได้จากข้อก่อนมา inner join พร้อมทั้งเขี่ยน script ในการเช็ค Duplicated Row และนับจำนวนคนที่มีทั้งหมด

In [0]:
# joined_df = profile_df.join(top_up_df,(profile_df.access_method_num == top_up_df.access_method_num) &
#                                        (profile_df.register_date == top_up_df.register_date),'left')
                            
joined_df = profile_df.join(top_up_df,['access_method_num','register_date'],'left')
                            
                                            

In [0]:
joined_df.display()

access_method_num register_date network_type arpu_thb mou_minute vou_mb voice_user sum_face_value avg_face_value no_recharge_date ++.QugxQ10Gk+49dwbFgy3ap1rHaWPp8WoebuyIO481mnrwZoD0.FLzI2CZ4Gqyq 2014-02-21T00:00:00.000+0000 3GPre-paid 391.1800 7.5000 77075.8900 data_user 420.0 84.0 4 ++0XMHWF2nDsLFqOpS0srJlCBZ3vugUk9yTLe.PDe+ta4oU4kU8ePLw+PMaqrMuV 2016-05-25T00:00:00.000+0000 3GPre-paid 0.0000 0.0000 0.0000 low_usage null null null ++3wpQuRdgauRX5v7T222S+cFCstgzYQPtvVNOj08jwQK2NCynFPrDXvfDtpFOEU 2007-07-03T00:00:00.000+0000 3GPre-paid 328.2000 321.4300 0.0000 voice_user 200.0 200.0 1 ++5HOzPk5P59pbcHqQGNLnLCUHk+zkPAOxdoI9ICC47EngjxGU9iV0pbEB8J0WRg 2020-10-24T00:00:00.000+0000 3GPre-paid 0.0000 0.0000 0.0000 low_usage null null null ++6IWbOwW+l7FcAVCeNpKFQ1mIyBjZxeesBnWA51AxBz3Den2+rF0As.I8z0BR2c 2013-09-16T00:00:00.000+0000 3GPre-paid 169.8900 20.3500 5206.5500 heavy_user 160.0 32.0 5 ++8MBVpt65n4AGO1c9b8X1WaM0rKL07NXsCW22I9Q1yT4sBtj8Pbm536qnAo3A48 2021-10-10T00:00:00.000+0000 3GPre-paid 0.0000 0.0000 0.0000 low_usage 10.0 10.0 1 ++A.O3aTmAGZo5EQ1VvGzbiqXOLLfzVC9LqiBtCm1qgcYpEBI7zbs+oTBECvdDF4 2016-06-05T00:00:00.000+0000 3GPre-paid 0.0000 0.0000 0.0000 low_usage null null null ++FmPvTl4ANQbNybCAmEflOxXmumG9UhvugejX.W363rG4.k5+gqbQ0L67A6Gej3 2021-04-18T00:00:00.000+0000 3GPre-paid 0.0000 0.0000 0.0000 low_usage null null null ++GtQoYqrirnYt0BiEwIYOJNY0Cvyc7jJGoNxLtR+0vZDa4mzNylNEtKaMmz1u+E 2020-09-15T00:00:00.000+0000 3GPre-paid 27.8600 32.1400 0.0000 voice_user null null null ++J.O08d6zc.m1IPsFLOo9mytBrhygOb2KBNTC9dCub8ejtSgQy62+jL0e0+u9i2 2019-12-28T00:00:00.000+0000 3GPre-paid 0.0000 0.0000 0.0000 low_usage null null null ++JxB+3ukj93RZ7GXaVRVtZIAcIyTIMNPXpHeTTOHw0nXGDYU7c+76bjvbsfERBO 2018-10-29T00:00:00.000+0000 3GPre-paid 0.0000 0.0000 0.0000 low_usage null null null ++MB8Bc.u0Rlos5AOPfNXNS5XNECfZoSzPlvNt7KH59WENyugdKGT5I19cQzBBBc 2014-05-17T00:00:00.000+0000 3GPre-paid 0.0000 0.0000 0.0000 low_usage null null null ++OXbcjMYH9sU7TdksQvWZgxIo7WARi1vb89yDs305LOIIxEd+wmA7tXuhegvpbX 2019-12-21T00:00:00.000+0000 3GPre-paid 0.0000 0.0000 0.0000 low_usage null null null ++P8FSVdADEVW1nlSlNroodhZWRtOp+Ih5a4bzr9wY68z2bRf482dKuXFQ32E.Pf 2017-09-08T00:00:00.000+0000 3GPre-paid 25.5900 26.7800 0.0000 voice_user null null null ++PMUDm52Ppg9yjMpIChym5zE0NmBPgcqSBOGpsrBMMSbK.MoIIMvELLC1WaCaMj 2021-02-12T00:00:00.000+0000 3GPre-paid 0.0000 0.0000 0.0000 low_usage null null null ++Ql9VtfG6GlbjQdh7vozxIoe1uzYrbwEbQU2klTMEL.5Wbr6KSPDxpiXnrTCmzY 2021-06-13T00:00:00.000+0000 3GPre-paid 0.0000 0.0000 0.0000 low_usage null null null ++TRgIavkDS9oe7L4CUyL0UcjBTCOlocJr7PFIKIFUZ6CsFr0L0Qk2O5dkLLj17V 2017-11-12T00:00:00.000+0000 3GPre-paid 548.1200 94.2900 27600.9000 heavy_user 600.0 150.0 4 ++V6pVky1oiS6MCuY2HRrPr+sFZ.0FzSbUok5Ur+f9w0AVDAe36TTTHyLwgDbNdA 2020-02-11T00:00:00.000+0000 3GPre-paid 50.3600 2.1400 0.0000 low_usage 50.0 50.0 1 ++XcfRm8jG70Z.uTrfu.Hug1MAjo6L3LHfIRhSzpQ7ihHfZ637Q7.l4.36I1Xzap 2021-11-29T00:00:00.000+0000 3GPre-paid 0.0000 0.0000 0.0000 low_usage null null null ++Y+09nVgIj7pWeh97Ftoa5hUeCCxYM5ozdK0M5fMs2dNrvWpR5gLtc2slk5pbjj 2012-09-21T00:00:00.000+0000 3GPre-paid 17.6800 10.7200 0.0000 voice_user null null null ++ZGFQHha79oQptb74JikIRKVJRLyvvUawtTuEOE5fEVvrymTE7VGwd1A7BW1QAf 2020-07-21T00:00:00.000+0000 3GPre-paid 0.0000 0.0000 0.0000 low_usage null null null ++b9DO.nxH2oVLzaPOfH7.Mx9qIVWZohrctx35XADS2nZjuyCuEjAdRX2gCHJV43 2021-12-18T00:00:00.000+0000 3GPre-paid 0.0000 317.1400 94031.8400 heavy_user null null null ++cUZVqm6.bhY10l+.fOaCkEGwq4ERvCuwD7rLzRmFhD.xGwnaEs1U4Vj9ylZjHP 2022-02-10T00:00:00.000+0000 3GPre-paid 140.1900 363.1600 30252.1100 heavy_user null null null ++dMLF7mlfqYITbCzohmD6Dy8z3Y137diDPbl2LVcdViUiV5coqz1BnKYXNSZDrJ 2008-07-19T00:00:00.000+0000 3GPre-paid 4.0100 4.2900 0.0000 low_usage 20.0 20.0 1 ++ev3tydFPeY4cIeVwOGmDrpNOJtR6CTQ1rerW2Ns4k9wW4lGuFxdtGZhrbxoLMD 2021-11-17T00:00:00.000+0000 3GPre-paid 16.2100 19.2800 0.0000 voice_user null null null ++fDyoNt5EHzXk3z.MtlsdqPuRU2S79kDaMPMK0S4QQmC.FuUvQYgKd

In [0]:
joined_df.groupBy(['access_method_num','register_date'])\
    .count()\
    .where(col('count') > 1)\
    .select(F.sum('count'))\
    .show()

+----------+
sum(count)|
+----------+
 null|
+----------+

In [0]:
joined_df.count()

Out[80]: 36343958